<a href="https://colab.research.google.com/github/neerajpadarthi/Big-Data-Programming_Project/blob/master/Source/Hiresh/Model_Accuracy_Comparison.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!apt-get install openjdk-8-jdk-headless -qq > /dev/null

In [0]:
!wget -q http://www-eu.apache.org/dist/spark/spark-2.4.4/spark-2.4.4-bin-hadoop2.7.tgz

In [0]:
!tar xf spark-2.4.4-bin-hadoop2.7.tgz

In [11]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
!pip install -q findspark

In [0]:
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-2.4.4-bin-hadoop2.7"

In [0]:
import findspark
findspark.init()
from pyspark.sql import SparkSession
spark = SparkSession.builder.master("local[*]").getOrCreate()

In [0]:
from pyspark import SparkContext
from pyspark.streaming import StreamingContext
from pyspark.sql import SQLContext
from pyspark.sql.functions import desc
from pyspark.sql import Row
import re

In [0]:
"/content/drive/My Drive/bigdata/project/training.1600000.processed.noemoticon.csv"

In [28]:
import glob,csv
import pandas as pd
df = pd.concat([pd.read_csv(f, encoding='latin1', quoting=csv.QUOTE_NONE,error_bad_lines=False) \
                for f in glob.glob('/content/drive/My Drive/bigdata/project/training.1600000.processed.noemoticon.csv')])

b'Skipping line 8: expected 7 fields, saw 9\nSkipping line 15: expected 7 fields, saw 8\nSkipping line 43: expected 7 fields, saw 8\nSkipping line 52: expected 7 fields, saw 9\nSkipping line 56: expected 7 fields, saw 8\nSkipping line 64: expected 7 fields, saw 8\nSkipping line 82: expected 7 fields, saw 8\nSkipping line 88: expected 7 fields, saw 9\nSkipping line 90: expected 7 fields, saw 8\nSkipping line 95: expected 7 fields, saw 8\nSkipping line 106: expected 7 fields, saw 8\nSkipping line 125: expected 7 fields, saw 8\nSkipping line 133: expected 7 fields, saw 8\nSkipping line 157: expected 7 fields, saw 8\nSkipping line 164: expected 7 fields, saw 8\nSkipping line 195: expected 7 fields, saw 8\nSkipping line 225: expected 7 fields, saw 8\nSkipping line 252: expected 7 fields, saw 8\nSkipping line 279: expected 7 fields, saw 8\nSkipping line 287: expected 7 fields, saw 8\nSkipping line 294: expected 7 fields, saw 8\nSkipping line 302: expected 7 fields, saw 8\nSkipping line 333: 

In [43]:
df.head()

score  ...  that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D"
0   "0"  ...                                                NaN                      
1   "0"  ...                                                NaN                      
2   "0"  ...                                                NaN                      
3   "0"  ...   it's not behaving at all. i'm mad. why am i h...                      
4   "0"  ...                                                NaN                      

[5 rows x 7 columns]

In [0]:
df.rename(columns={'"@switchfoot http://twitpic.com/2y1zl - Awww':'tweet'},inplace=True)

In [0]:
df_col=df.drop(columns=['"1467810369"', '"Mon Apr 06 22:19:45 PDT 2009"','"NO_QUERY"','"_TheSpecialOne_"'])

In [54]:
df_col.head()

score  ...  that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D"
0   "0"  ...                                                NaN                      
1   "0"  ...                                                NaN                      
2   "0"  ...                                                NaN                      
3   "0"  ...   it's not behaving at all. i'm mad. why am i h...                      
4   "0"  ...                                                NaN                      

[5 rows x 3 columns]

In [0]:
df_filtered=df_col[df_col['tweet'].str.contains("sport")|df_col['tweet'].str.contains("cricket")|df_col['tweet'].str.contains("cricket")\
       |df_col['tweet'].str.contains("football")|df_col['tweet'].str.contains("baseball")\
       |df_col['tweet'].str.contains("badminton")|df_col['tweet'].str.contains("golf")\
       |df_col['tweet'].str.contains("hockey")|df_col['tweet'].str.contains("tennis")]

In [74]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.pylab import rcParams
df_filtered['sentiment_description']=np.where(df_filtered.score=='"0"','negative','positive')

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [75]:
df_filtered.head()

score  ... sentiment_description
71     "0"  ...              negative
171    "0"  ...              negative
406    "0"  ...              negative
1058   "0"  ...              negative
1563   "0"  ...              negative

[5 rows x 4 columns]

In [76]:
print(df_filtered.score.value_counts(),'\n\n',df_filtered.sentiment_description.value_counts())

"0"    2641
"4"    2432
Name: score, dtype: int64 

 negative    2641
positive    2432
Name: sentiment_description, dtype: int64


In [0]:
from sklearn.model_selection import train_test_split
train, test = train_test_split(df_filtered,test_size=0.3)

In [0]:
train_corpus = []
test_corpus = []
model_corpus=[]
for each in train['tweet']:
    train_corpus.append(each)
for each in test['tweet']:
    test_corpus.append(each)
for each in df_filtered['tweet']:
    model_corpus.append(each)

## Start creating them
from sklearn.feature_extraction.text import TfidfVectorizer
v = TfidfVectorizer(stop_words='english',strip_accents='unicode',
                                    token_pattern=r'\w{2,}')
train_features = v.fit_transform(train_corpus)
test_features=v.transform(test_corpus)
model_features = v.transform(model_corpus)

In [114]:
print(train_features.shape)
print(test_features.shape)
print(model_features.shape)

(3551, 7815)
(1522, 7815)
(5073, 7815)


In [0]:
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix

In [0]:
Classifiers = {'lg':LogisticRegression(random_state=42,C=5,max_iter=200),\
               'dt':DecisionTreeClassifier(random_state=42,min_samples_leaf=1),\
               'rf':RandomForestClassifier(random_state=42,n_estimators=100,n_jobs=-1),\
               'gb':GradientBoostingClassifier(random_state=42,n_estimators=100,learning_rate=0.3)}

In [0]:
def ML_Pipeline(clf_name):
    clf = Classifiers[clf_name]
    fit = clf.fit(train_features,train['sentiment_description'])
    pred = clf.predict(test_features)
    Accuracy = accuracy_score(test['sentiment_description'],pred)
    Confusion_matrix = confusion_matrix(test['sentiment_description'],pred)
    print('==='*35)
    print('Accuracy of '+ clf_name +' is '+str(Accuracy))
    print('==='*35)
    print(Confusion_matrix)
    return clf

In [99]:
model=ML_Pipeline('lg')

Accuracy of lg is 0.6892247043363995
[[562 241]
 [232 487]]


/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


In [0]:
from sklearn.metrics import accuracy_score

In [88]:
from textblob import TextBlob
df_filtered['sentiment_value']=df_filtered.tweet.apply(lambda x:TextBlob(str((x).encode('ascii', 'ignore'))).sentiment.polarity)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [89]:
df_filtered['textblob_score']=np.where(df_filtered.sentiment_value<=0.0,1,0)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [90]:
df_filtered['tbsentiment_description']=np.where(df_filtered.textblob_score<=0.0,'negative','positive')

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [91]:
accuracy_score(df_filtered['sentiment_description'], df_filtered['tbsentiment_description'])

0.40015769761482356

In [117]:
df_filtered["model_description"]=model.predict(model_features)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [118]:
accuracy_score(df_filtered['sentiment_description'], df_filtered['model_description'])

0.8825152769564361